In [0]:
%pip install Faker==37.4.0 

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%pip install dbldatagen==0.4.0.post1

Note: you may need to restart the kernel using %restart_python or dbutils.library.restartPython() to use updated packages.


In [0]:
%restart_python

🔥 Backstory: The Phoenix101 Legacy

When the Securehome first launched its insurance platform back in 2015, they had limited resources. There was no dedicated data team, no warehouse, so they started off with Excel sheets.

As they gradually matured, they had a small engineering group managing a basic PostgreSQL database and dumping CSVs for backups and ad hoc reporting.

The system that handled user signups internally was known as "Phoenix101", a monolithic service built quickly to meet tight go-to-market deadlines. It worked… but barely.
🗂️ How the Data Was Managed

    Users signed up through a basic web form.

    Data was stored in a PostgreSQL table called users, but there was no clear process for exports, backups, or archiving.

    Engineers would occasionally export slices of the table into CSVs for backup, analytics, or handover to business teams.

📉 Where Things Went Wrong

By 2017, the platform had changed so much that Phoenix101 was being phased out. However, due to legal requirements, user data needed to be retained.

The team exported everything to CSVs using psql and Excel — manually, across different machines and time zones.
Here's what went sideways:

    Some engineers used COPY commands directly from PostgreSQL with YYYY-MM-DD formatting.

    Others used Excel to open and re-save the exports, introducing locale-based date shifts:

        U.S.-based engineers saved dates as MM/DD/YYYY

        UK/Europe-based engineers had DD/MM/YYYY

    A few batch exports were corrected manually over phone calls with users who claimed their names or emails were spelled incorrectly — those changes were made directly in Excel.

No versioning. No rollback plan.
🛠️ What Was Preserved

Only a handful of fields made it into the export:

    user_id was reliable — it came from an auto-incremented field in the DB.

    firstname, lastname, and email_address were sometimes corrected but not standardized.

    created_at was wildly inconsistent depending on the file batch.

    ingestion_timestamp was added later — it records when the dump was finally uploaded to cloud storage during the company’s data platform migration in 2021.

    source_system was hardcoded as "PHOENIX101" to indicate it came from the legacy system.

📦 Why It Matters Now

Now, in 2025, the company is modernizing its entire data infrastructure. They're moving everything into Databricks and trying to reconcile these legacy CSVs with newer, cleaner systems.

An intern is tasked with loading and validating this phoenix101 dataset — and quickly realizes that although user_id looks consistent, nothing else can be trusted blindly.

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, LongType, TimestampType, DateType, IntegerType

# The schema for users
# Had to call to change information
# maually done with excel

# batches of created_at were different in export a different format

phoenix101_schema = StructType([
    StructField("user_id", IntegerType(), False),
    StructField("firstname", StringType(), False),
    StructField("lastname", StringType(), False),
    StructField("email_address", StringType(), False),
    StructField("phone_number", StringType(), False),
    StructField("created_at", TimestampType(), False),
    StructField("ingestion_timestamp", DateType(), False),
    StructField("source_system", StringType(), False)
    ]
)


In [0]:
import random
from pyspark.sql.functions import udf
import re
import string

# Set seed for reproducibility
SEED_NUMBER = 42
random.seed(SEED_NUMBER)

def random_space() -> str:
    """
    Generates a random space character

    Returns:
        str: A random space character
    """
    return random.choice(["", " ", "   "])

def filter_remove_unwanted_characters(local_part: str) -> str:
    """
    Filters out unwanted characters from the local part of an email address.

    Args:
        local_part (str): The local part of an email address.

    Returns:
        str: The filtered local part of an email address.
    """
    local = re.sub(r"[^A-Za-z0-9._+\-']", "", local_part)
    return re.sub(r"\.+", ".", local).strip(".")

def random_local_part(firstname: str, lastname: str, min_length: int = 6) -> str:
    """
    Generates a random local part for an email address with better randomness
    and avoids very short predictable outputs.

    Args:
        firstname (str): The firstname of the user.
        lastname (str): The lastname of the user.
        min_length (int): Minimum length of the local part.

    Returns:
        str: The generated local part for an email address.
    """

    firstname = filter_remove_unwanted_characters(firstname or "").lower()
    lastname = filter_remove_unwanted_characters(lastname or "").lower()

    # Pick random slice lengths (at least 2 chars if possible)
    fn_slice = firstname[: random.randint(2, len(firstname))] if firstname else ""
    ln_slice = lastname[: random.randint(2, len(lastname))] if lastname else ""

    # Random numeric or alphanumeric tail
    tail = ''.join(random.choices(string.ascii_lowercase + string.digits, k=6))

    # Combine and shuffle pieces
    parts = [fn_slice, ln_slice]
    random.shuffle(parts)
    parts.append(tail)
    local_part = "".join(parts)

    # Enforce minimum length by padding with random chars
    while len(local_part) < min_length:
        local_part += random.choice(string.ascii_lowercase + string.digits)

    return local_part


@udf("string")
def create_email_address(firstname, lastname, domain):
    error_space = random_space()
    return random_local_part(firstname, lastname) + error_space + '@' + domain


In [0]:
import dbldatagen as dg
from dbldatagen import DataGenerator, fakerText, FakerTextFactory
import pyspark.sql.functions as F
from faker import Faker
from faker.providers import internet
from pyspark.sql import Window


fake = Faker(locale="UK")
Faker.seed(SEED_NUMBER)
FakerTextUK = FakerTextFactory(locale=["en_UK"], providers=["internet"])

source_systems = ["PHOENIX101", "PHOENIX-1"]

@udf("string")
def generate_antonburg_phone(n: int) -> str:
    rand_val = random.random()
    if rand_val <= 0.5:
        return f"0543-000-{n:07d}"
    else:
        return f"0543000{n:07d}" + random_space()


In [0]:
partitions_requested = 8
data_rows = 5_000_000

spark.conf.set("spark.sql.shuffle.partitions", partitions_requested)


phoenix101_faker_dataspec = (
    dg.DataGenerator(spark, rows=data_rows, startingId=1, partitions=partitions_requested)
    .withIdOutput()
    .withSchema(phoenix101_schema)
)

phoenix101_faker_dataspec = (
    phoenix101_faker_dataspec.withColumnSpec(
        "firstname", text=FakerTextUK("first_name")
    )
    .withColumnSpec("lastname", percentNulls=0.1, text=FakerTextUK("last_name"))
    .withColumnSpec("phone_number", percentNulls=0.23, text=FakerTextUK("phone_number"))
    .withColumnSpec(
        "created_at",
        data_range=dg.DateRange(
            "2017-06-01 01:33:00", "2018-01-01 01:33:00", "1 minute"
        ),
        random=True,
    )
    .withColumnSpec("ingestion_timestamp", values=["2018-06-12 02:15:00"])
    .withColumnSpec("source_system", values=["PHOENIX101"])
)

df_phoenix101_faker = phoenix101_faker_dataspec.build()


df_phoenix101_faker = df_phoenix101_faker.withColumn("domain_name", F.lit("example.com")).withColumn(
    "email_address", create_email_address("firstname", "lastname", "domain_name")
)
df_phoenix101_faker = df_phoenix101_faker.withColumn(
    "phone_number", generate_antonburg_phone("id")
)

schema_cols = [field.name for field in phoenix101_schema.fields]

# Select those columns from the DataFrame
df_phoenix101_faker_selected = df_phoenix101_faker.select(*schema_cols)
display(df_phoenix101_faker_selected)

user_id firstname lastname email_address phone_number created_at ingestion_timestamp source_system 1 Jack Norton jacknorto5fyjbq @example.com 05430000000001 2017-07-04T21:54:00.000Z 2018-06-12 PHOENIX101 2 Brandon Harper harpebrandonw4hwd3@example.com 0543-000-0000002 2017-07-16T00:45:00.000Z 2018-06-12 PHOENIX101 3 Stephanie Jackson stephanja7179ml@example.com 05430000000003 2017-11-28T01:05:00.000Z 2018-06-12 PHOENIX101 4 Marc Skinner skinnemarrwxnhz @example.com 0543-000-0000004 2017-11-18T00:52:00.000Z 2018-06-12 PHOENIX101 5 Benjamin Baker benjbakhlqklo@example.com 0543-000-0000005 2017-06-02T16:22:00.000Z 2018-06-12 PHOENIX101 6 Steven Bishop stebiqc4d3o @example.com 0543-000-0000006 2017-08-28T08:51:00.000Z 2018-06-12 PHOENIX101 7 Conor James conojamene23p @example.com 05430000000007 2017-07-15T01:41:00.000Z 2018-06-12 PHOENIX101 8 June Bull bujugyddyc @example.com 05430000000008 2017-12-17T03:55:00.000Z 2018-06-12 PHOENIX101 9 Joshua Lucas joslucac58tsg@example.com 0543-000-0000009 2017-12-24T22:53:00.000Z 2018-06-12 PHOENIX101 10 Vincent Mellor melvikxv557 @example.com 05430000000010 2017-06-10T00:42:00.000Z 2018-06-12 PHOENIX101 11 Eleanor Young eleanoryo04dkcz @example.com 0543-000-0000011 2017-09-06T02:03:00.000Z 2018-06-12 PHOENIX101 12 Tony Todd tototc2mib@example.com 05430000000012 2017-10-07T05:31:00.000Z 2018-06-12 PHOENIX101 13 Harry Wallis wallisharryab1z0t@example.com 0543-000-0000013 2017-10-25T16:34:00.000Z 2018-06-12 PHOENIX101 14 Anna Price pricanud98q3@example.com 05430000000014 2017-06-10T12:59:00.000Z 2018-06-12 PHOENIX101 15 Patricia null patr6ou09v @example.com 05430000000015 2017-11-09T08:47:00.000Z 2018-06-12 PHOENIX101 16 Sam Jordan sajor4hx31h @example.com 05430000000016 2017-08-04T09:31:00.000Z 2018-06-12 PHOENIX101 17 Patricia Oliver patroliqgf0wp @example.com 0543-000-0000017 2017-12-02T22:05:00.000Z 2018-06-12 PHOENIX101 18 Gordon Nolan nogordonyhgd0f @example.com 0543-000-0000018 2017-06-08T09:18:00.000Z 2018-06-12 PHOENIX101 19 Craig Hughes craighughstejio@example.com 0543-000-0000019 2017-10-23T10:26:00.000Z 2018-06-12 PHOENIX101 20 Yvonne null yvfxxzqk @example.com 0543-000-0000020 2017-11-12T17:53:00.000Z 2018-06-12 PHOENIX101 21 Donna Cox codone8e8p6 @example.com 0543-000-0000021 2017-09-29T17:25:00.000Z 2018-06-12 PHOENIX101 22 Emily Hargreaves emilharga1fwdk@example.com 0543-000-0000022 2017-12-06T08:39:00.000Z 2018-06-12 PHOENIX101 23 Edward Smith edwsmix0owom @example.com 05430000000023 2017-07-29T17:59:00.000Z 2018-06-12 PHOENIX101 24 Clare Woods clarewoode7jgr9@example.com 0543-000-0000024 2017-11-01T18:32:00.000Z 2018-06-12 PHOENIX101 25 Tom Young tomyoun3s34em @example.com 05430000000025 2017-11-11T09:41:00.000Z 2018-06-12 PHOENIX101 26 Allan Williams allanwilcuaf9c@example.com 05430000000026 2017-06-30T05:40:00.000Z 2018-06-12 PHOENIX101 27 Kevin Sharpe shakevxkrifh@example.com 0543-000-0000027 2017-07-06T08:32:00.000Z 2018-06-12 PHOENIX101 28 Marilyn Roberts marojzy21t @example.com 0543-000-0000028 2017-08-07T22:49:00.000Z 2018-06-12 PHOENIX101 29 Gavin Myers gamyers22f98o@example.com 05430000000029 2017-10-31T01:13:00.000Z 2018-06-12 PHOENIX101 30 Debra Hayes hayesdenuztgv@example.com 05430000000030 2017-12-28T12:12:00.000Z 2018-06-12 PHOENIX101 31 Shane Warner warshanemrd8i2@example.com 05430000000031 2017-08-21T02:02:00.000Z 2018-06-12 PHOENIX101 32 Victor Collins victococ0w5s0 @example.com 0543-000-0000032 2017-07-07T01:49:00.000Z 2018-06-12 PHOENIX101 33 Samuel Johnson samujohnbunpoi @example.com 05430000000033 2017-08-13T08:58:00.000Z 2018-06-12 PHOENIX101 34 Jacob Whittaker whittjaw9j0ba @example.com 05430000000034 2017-07-26T18:18:00.000Z 2018-06-12 PHOENIX101 35 Shannon null shannoc4ef5r@example.com 05430000000035 2017-12-09T02:03:00.000Z 2018-06-12 PHOENIX101 36 Terence Dyer tedyerw4h7gy@example.com 05430000000036 2017-07-15T16:34:00.000Z 2018-06-12 PHOENIX101 37 Diane Smith dismit35ntxf @example.com 0543-000-0000037 2017-10-02T00:25:00.000Z 2018-06-12 PHOENIX101 3

In [0]:
%sql
DROP TABLE IF EXISTS securehome.raw.phoenix101_faker;

In [0]:
df_phoenix101_faker_selected.write.mode("overwrite").option("mergeSchema", "true").saveAsTable("securehome.raw.phoenix101_faker")

In [0]:
%sql
with temp AS (
SELECT email_address, COUNT(email_address) counter
FROM securehome.raw.phoenix101_faker
GROUP BY email_address
)

SELECT *
FROM temp
ORDER BY counter DESC


email_address counter joepan5mrng@example.com 1 alanjo3j9sfx@example.com 1 shansmithib6qjg @example.com 1 brcooknbclqd @example.com 1 nathhcvbas@example.com 1 trwaapvvek@example.com 1 leaaustzk4pu9 @example.com 1 turnegeor5n0ms6 @example.com 1 wilsonelev5yint @example.com 1 kennetcarzfzcyp @example.com 1 fiofre5yl3rq @example.com 1 valhat5m96k @example.com 1 cherrihz5x@example.com 1 dannygreeno1w7or @example.com 1 daviessheiu9ghne @example.com 1 willialexandrrsw65j @example.com 1 tonqj0lj9 @example.com 1 mathewgismaqts @example.com 1 wayndaviahwq1j @example.com 1 tasa7sgs2e @example.com 1 gregor1mkwax@example.com 1 cljac5k65dx @example.com 1 whitrertdmqn@example.com 1 breevai8b2ga @example.com 1 brookeamlipwnl @example.com 1 trevochapmanqa72od @example.com 1 puggemmmvgimk@example.com 1 gemarpnz0v6@example.com 1 ge7mqf82 @example.com 1 tayanne6zdbzd @example.com 1 marikel9xuebz@example.com 1 arlouikucrg7@example.com 1 geraln6mkff @example.com 1 goraepeki @example.com 1 gardnesar8nc4jx@example.com 1 aliuqs8js@example.com 1 stachuk9lt33 @example.com 1 owenjean8xvjeo @example.com 1 karlwilliauo6ige @example.com 1 stephensvija0qhm@example.com 1 joneangelac4oo8t@example.com 1 marcumurpkgdlwd @example.com 1 jessicpwvbss @example.com 1 kepotts907dq@example.com 1 rejovfc8fn@example.com 1 philhucx3aun @example.com 1 christopsmmnspn0 @example.com 1 brownliamuqbu73 @example.com 1 derha85jv8u @example.com 1 sh5ui0tb @example.com 1 fulmegjt66a8 @example.com 1 kevinpaa3mqi1 @example.com 1 stegriffithokb9rg @example.com 1 declawal6laasl@example.com 1 ellevan608iod@example.com 1 warneirv0zi0 @example.com 1 kimberpereacbfu @example.com 1 ellijonesfqsl94@example.com 1 aarmartinfrrn7t@example.com 1 mewestv0tisq @example.com 1 daalisoisicb2@example.com 1 rosebrigp8p6gc @example.com 1 murstuarqopbwx @example.com 1 rahmanalics67g8r @example.com 1 hayleburk8dqyv @example.com 1 robfra2ugkb @example.com 1 nicholsonwendqg0ik9 @example.com 1 tipaym7nhc@example.com 1 smitgemmbtp0f5 @example.com 1 caronor5ebc5f @example.com 1 leslewilt7ulv0 @example.com 1 joda8mwo2s @example.com 1 emcl5k1quv @example.com 1 stephatylzny3mr @example.com 1 hammonrico31aot @example.com 1 aljeffrehim0h6 @example.com 1 elbirchlm0hnd@example.com 1 hajaswfx4bk @example.com 1 amayoung8v1w6l@example.com 1 lyndabar94pouy @example.com 1 pateashleivu9cxr @example.com 1 philicooperdlhd5r @example.com 1 gaandpybsa3 @example.com 1 deoliver06r1ao @example.com 1 mohambaker0doltm @example.com 1 austmax162v0d @example.com 1 alkivkftt8 @example.com 1 chl529dy @example.com 1 marshav7aizr@example.com 1 jemhard6kxi53@example.com 1 adamwarrjeq2l @example.com 1 womanzwc7np @example.com 1 davisonpatm8roc5 @example.com 1 richardsonviyphn1m @example.com 1 marcwillis1dyihm @example.com 1 amhuntalt2m9 @example.com 1 thompsonrhikf1mi@example.com 1 smieliyr7eez @example.com 1 holdendy7441g0@example.com 1 lydiahardq9ztr@example.com 1 davcarjk3i7e@example.com 1 geoeile1bs48e@example.com 1 nelsjulit45jf8@example.com 1 jacjenkipbmzvh @example.com 1 salchaddi7bw @example.com 1 tocarlnwdli8 @example.com 1 hilldorotpv3rv3 @example.com 1 greperkinkd484r @example.com 1 wrightfrb0mpjk@example.com 1 rita9lyz90 @example.com 1 chapmajoadrnm9x @example.com 1 thomdylanf9vl6h@example.com 1 webstegax2s6kk @example.com 1 mikaty8yropi @example.com 1 stacepoojvgtc4 @example.com 1 thomadanine3u2v @example.com 1 crophilvh18s8 @example.com 1 joknowtjdi8o @example.com 1 marirojwl0sx@example.com 1 crosvicoblj0z@example.com 1 brownleiw7e13 @example.com 1 melanah861t5q @example.com 1 juliewoodwjma0hh@example.com 1 fishemo3c525k @example.com 1 johnsmegasbjsik @example.com 1 hamiltonlouiserpocrh@example.com 1 maxricha04fsjn@example.com 1 toowen499k0g@example.com 1 hughbrandoncbclqt @example.com 1 thomwill0qyxm6 @example.com 1 sarawil164bd4 @example.com 1 eltay7z82kr @example.com 1 nichowatu3mpau @example.com 1 blackmart53bw4@example.com 1 simden2vp4pw@example.com 1 wyattstev4rr5f5@example.com 1 josmit0cqy2u@example.com 1 simocotz8kiq